# Prepare Environment

Load necessary modules and attempt to compile the GrOpt library if it isn't already

In [1]:
%load_ext watermark

# This attempts to re-compile the library in case it has been changed, mostly for debug, but won't do anything
# if nothing is changed
import build_gropt
build_gropt.build_gropt()
import gropt

from helper_utils import *
from interactive_plots import plot_waveform_interactive
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from IPython.core.display import display, HTML
init_notebook_mode(connected = True)
config={'showLink': False, 'displayModeBar': False}
from timeit import default_timer as timer

%matplotlib inline

Building GrOpt . . .


Print all used libraries and system info, so as to enable reproducibility

In [2]:
%watermark -v -m -p watermark,pandas,numpy,matplotlib,chart_studio,cufflinks,seaborn,plotly
print()
%watermark -u -n -t -z

Python implementation: CPython
Python version       : 3.7.9
IPython version      : 7.19.0

watermark   : 2.1.0
pandas      : 1.0.1
numpy       : 1.18.1
matplotlib  : 3.1.3
chart_studio: 1.1.0
cufflinks   : 0.17.3
seaborn     : 0.10.0
plotly      : 4.14.3

Compiler    : MSC v.1916 64 bit (AMD64)
OS          : Windows
Release     : 10
Machine     : AMD64
Processor   : Intel64 Family 6 Model 142 Stepping 9, GenuineIntel
CPU cores   : 4
Architecture: 64bit


Last updated: Sun Jan 31 2021 20:46:09Central European Standard Time



### Test the function for ploting interactive figures

Define a function for generating test cases and ploting them using the plot_waveform_interactive function found in interactive_plots.py

In [3]:
def make_testcase_simpdiff(gmax, smax, MMT, TE, T_readout, T_90, T_180, diffmode, mode, dt=-1, N = -1):

    params_in = {}
    params_in[u'gmax'] = gmax
    params_in[u'smax'] = smax
    params_in[u'MMT'] = MMT
    params_in[u'TE'] = TE
    params_in[u'T_readout'] = T_readout
    params_in[u'T_90'] = T_90
    params_in[u'T_180'] = T_180
    params_in[u'diffmode'] = diffmode
    params_in[u'mode'] = mode
    params_in[u'dt'] = dt
    params_in[u'N'] = N
    
    if (dt < 0) and (N < 0):
        print('ERROR: dt or N needs to be set for test case')
    elif (dt > 0):
        start = timer()
        G, dd = gropt.gropt(params_in, verbose=1)
        end = timer()
    elif (N > 0):
        start = timer()
        G, dd = gropt.gropt(params_in, verbose=1)
        end = timer()
    
    testcase = {}
    
    # This is referencing the testcase setup, not the software version
    testcase[u'version'] = 'diff_v1'
    
    testcase[u'params_in'] = params_in
    testcase[u'G'] = G
    testcase[u'dd'] = dd[:32]
    testcase[u'compute_time'] = end-start
    
    return testcase

#### Set parameters

In [4]:
# Repeat entire script with different moments
all_testcase = []
gmax = .08      # Gmax in [T/s]
smax = 200      # Slew max im [T/m/s]
TE = 44.4       # TE in [ms]
T_readout = 12  # [ms]
T_90 = 2        # [ms]
T_180 = 6       # [ms]
diffmode = 1    # diffmode =1 for beta-max, =2 for b-val max
mode = 'diff_bval'

#### Zero moment

In [6]:
MMT = 0
dt_range = np.array([.1, .2, .4, .5, .8, 1.0, 1.5, 2.0]) * 1.0e-3 # gradient raster time in [s]

for dt in dt_range:

    testcase = make_testcase_simpdiff(gmax, smax, MMT, TE, T_readout, T_90, T_180, diffmode, mode, dt=dt)
    all_testcase.append(testcase)
    fig = plot_waveform_interactive(testcase['G'], testcase['params_in'])
    fig.show()

#### First moment

In [7]:
MMT = 1
dt_range = np.array([.1, .2, .4, .5, .8, 1.0, 1.5, 2.0]) * 1.0e-3 # gradient raster time in [s]

for dt in dt_range:

    testcase = make_testcase_simpdiff(gmax, smax, MMT, TE, T_readout, T_90, T_180, diffmode, mode, dt=dt)
    all_testcase.append(testcase)
    fig = plot_waveform_interactive(testcase['G'], testcase['params_in'])
    fig.show()

#### Second moment

In [5]:
MMT = 2
dt_range = np.array([.1, .2, .4, .5, .8, 1.0, 1.5, 2.0]) * 1.0e-3 # gradient raster time in [s]

for dt in dt_range:

    testcase = make_testcase_simpdiff(gmax, smax, MMT, TE, T_readout, T_90, T_180, diffmode, mode, dt=dt)
    all_testcase.append(testcase)
#     print(testcase)
    fig = plot_waveform_interactive(testcase['G'], testcase['params_in'])
    fig.show()